# Testfile of the simulation-based scaling factors

### Modules

In [1]:
import numpy as np
import pandas as pd
import sys
import os
from itertools import product
from sklearn.metrics import normalized_mutual_info_score as nmi
import plotly.offline as pyo
from astropy.coordinates import ICRS, GalacticLSR
import astropy.units as u

from SigMA.SigMA import SigMA
from Loop_functions import setup_ICRS_ps, remove_field_stars, extract_signal_remove_spurious, extract_signal
from IsochroneArchive.myTools import my_utility
from PlotlyResults import plot

### Functions

In [2]:
def noise_generator(N_signal: int, signal_to_noise: float, ranges: np.array):
    N_noise = int(N_signal / signal_to_noise)
    # print(N_noise)
    uniform_distribution = np.vstack([np.random.uniform(min_val, max_val, size=N_noise) for min_val, max_val in
                                      ranges]).T

    return uniform_distribution

In [3]:
def spherical2GalacticLSR(spherical_data):

    coord = ICRS(
        ra=spherical_data[0] * u.deg, dec=spherical_data[1] * u.deg, distance=spherical_data[2] * u.pc,
    )
    d = coord.transform_to(GalacticLSR())
    d.representation_type = 'cartesian'

    return [d.x.value, d.y.value, d.z.value]

In [4]:
def scale_factors(filepath: str, c_solution: int):

    if c_solution == 6:
        stds = np.genfromtxt(filepath, usecols=(1,2,3), skip_header=2,max_rows=5)
    elif c_solution == 4:
        stds = np.genfromtxt(filepath, usecols=(1,2,3), skip_header=10, max_rows=5)
    else:
        print("Only 4C and 6C solutions available at the moment")
        stds = None

    sfs = np.empty(shape=(5,3))
    for h, row in enumerate(stds[:]):
        flipped_row = row[::-1]
        sfs[h] = 1/flipped_row

    return sfs

### Paths

In [5]:
# set sys and output paths
sys.path.append('/Users/alena/PycharmProjects/Sigma_Orion')
output_path = my_utility.set_output_path(main_path='/Users/alena/Library/CloudStorage/OneDrive-Personal/Work/PhD/Projects/Sigma_Orion/Coding/Code_output/')

In [6]:
# print the parameter choices into log-textfile into the right folder
########
run = "SF-6C-consensus"
########
if not os.path.exists(output_path + f"Run_{run}/"):
    os.makedirs(output_path + f"Run_{run}/")

output_path = output_path + f"Run_{run}/"

In [7]:
# read in data
labeled_clusters = pd.read_csv(
    "/Users/alena/PycharmProjects/SigMA_Orion/Start_data/Region_0/Simulated_clusters_labeled_Region0_run6.csv")

### Reference solution

In [8]:
# Enable notebook mode
pyo.init_notebook_mode(connected=True)

# Plot the "true" solution of the artificially generated clusters for reference
labels_generated = labeled_clusters.label.to_numpy()
fig1 = plot(labels_generated, labeled_clusters, "Solution_generated_clusters", output_path, icrs=True, return_fig=True)

pyo.iplot(fig1)

## 1. Noise

**Note:** As per 22-11-23, the noise is generated by extending the range of the simulated clusters by 30 %.

**Note:** It could be that the region is too large (see density histograms of 13-11-23, 14-11-23), so another starting point would be to take the range of the simulated clusters and artificially extend it by 10-20 %.

In [9]:
cols = ["ra", "dec", "plx", "pmra", "pmdec"]
noise_range = [(min(labeled_clusters[c])-np.ptp(labeled_clusters[c])*0.3, max(labeled_clusters[c])+np.ptp(labeled_clusters[c])*0.3) for c in cols]

In [10]:
# define SNR and 5D uniform distribution
sn = 0.2

unif = pd.DataFrame(data=noise_generator(labeled_clusters.shape[0], sn, noise_range),
                    columns=["ra", "dec", "plx", "pmra", "pmdec"]).assign(label=0)  # do not go smaller than 0.005


In [11]:
# Generate XYZ data for bg sources
XYZ_df = pd.DataFrame(np.column_stack(spherical2GalacticLSR([unif.ra, unif.dec, 1000 / unif.plx])), columns=["X", "Y", "Z"])

# Concatenate the ICRS DataFrame and the XYZ DataFrame
unif_full = pd.concat([unif, XYZ_df], axis=1)
unif_full.head()

ra        dec       plx      pmra     pmdec  label           X  \
0  85.888636   2.731076  2.959351  2.878656 -7.543745      0 -303.169016   
1  87.720177 -10.856514  3.102166 -2.347269  4.641471      0 -247.613650   
2  80.830230  -6.774761  1.676941  1.885885  5.919856      0 -481.747325   
3  88.731551   2.009087  3.315704  0.520576 -3.521794      0 -268.679768   
4  87.028251 -14.200693  1.169663 -1.049072  0.026847      0 -623.830972   

            Y           Z  
0 -125.772034  -80.339332  
1 -179.846148 -101.271068  
2 -265.964056 -229.749654  
3 -122.848233  -60.655521  
4 -503.625469 -296.867664

In [12]:
# merge the signal data with the noise data
merged_df = pd.merge(labeled_clusters, unif_full, on=['ra', 'dec', 'plx', 'pmra', 'pmdec', 'label', 'X', 'Y', 'Z'], how='outer')
merged_df.head()

Unnamed: 0         ra       dec       plx      pmra     pmdec           X  \
0         0.0  85.272399 -9.824571  2.266731  0.100548 -1.519346 -343.930798   
1         1.0  85.022205 -9.685002  2.218850  0.539925 -1.374314 -352.001449   
2         2.0  85.894114 -8.941628  2.352214  0.790936 -1.039383 -335.550990   
3         3.0  85.920994 -8.947240  2.260273  0.529628 -1.114190 -349.175038   
4         4.0  85.475184 -9.496668  2.191001  0.547853  0.181541 -357.473022   

            Y           Z  label  
0 -231.235006 -151.220450      0  
1 -234.463381 -155.684980      0  
2 -220.834445 -139.192076      0  
3 -229.954044 -144.697166      0  
4 -238.322290 -154.038555      0

In [13]:
# Check noise and signal 3D distribution
import plotly.express as px

fig = px.scatter_3d(merged_df, x='ra', y='dec', z='plx',
              color='label')
# pyo.plot(fig)

## 2. SigMA parameters

In [14]:
# define fixed SigMA parameters
step = 2
alpha = 0.05
beta = 0.99
knn_initcluster_graph = 35
knn = 30
bh = False
n_resampling = 0
scaling = None

feature_space = ['ra', 'dec', 'plx', 'pmra', 'pmdec']

## 2.1. Scale factors

In [15]:
std_path = "/Users/alena/PycharmProjects/SigMA_Orion/Start_data/Region_0/simulated_sfs.txt"
ra_scaling, dec_scaling, plx_scaling, pmra_scaling, pmdec_scaling = scale_factors(std_path, 6)

# create the 243 possible combinations
combinations = np.array(list(product(ra_scaling, dec_scaling, plx_scaling, pmra_scaling, pmdec_scaling)))

## 3. Evaluate Scale factor grid

In [16]:
# initialize SigMA for computational efficiency

setup_kwargs, df_focus = setup_ICRS_ps(df_fit=merged_df, sf_params=['ra', 'dec', 'plx'], sf_range=[ra_scaling, dec_scaling, plx_scaling], KNN_list=[knn], beta=beta, knn_initcluster_graph=knn_initcluster_graph, scaling=scaling)

sigma_kwargs = setup_kwargs["sigma_kwargs"]
scale_factor_list = setup_kwargs["scale_factor_list"]


In [17]:
# initialize SigMA with sf_mean for computational efficiency
clusterer = SigMA(
        data = df_focus, **sigma_kwargs)

In [18]:
outer = np.empty(shape=(len(combinations),6))
#outer_names = []

# Evaluate every grid point
for j, combo in enumerate(combinations[:]):

    print(f"--- Gridpoint {j} ---")

    scale_factors = {'pos': {'features': ['ra', 'dec', 'plx'], 'factor': list(combo[:3])},
                     'vel': {'features': ['pmra', 'pmdec'], 'factor': list(combo[3:])}}
    #                 'vel': {'features': ['pmra', 'pmdec'], 'factor': [0.5,0.5]}}
    clusterer.set_scaling_factors(scale_factors)
    print(f"Performing clustering for scale factor {clusterer.scale_factors['pos']['factor']}...")

    # Fit
    clusterer.fit(alpha=alpha, knn=knn, bh_correction=bh)
    label_array = clusterer.labels_
    # density and X
    rho, X = clusterer.weights_, clusterer.X

    label_matrix_rfs = np.empty(shape=(1, len(df_focus)))
    label_matrix_rsc = np.empty(shape=(1, len(df_focus)))
    label_matrix_simple = np.empty(shape=(1, len(df_focus)))

    # a) remove field stars
    nb_rfs = remove_field_stars(label_array, rho, label_matrix_rfs, 0)
    # b) remove spurious clusters
    nb_es, nb_rsc = extract_signal_remove_spurious(df_focus, label_array, rho, X, label_matrix_rsc, 0)
    # c) extract signal
    nb_simple = extract_signal(label_array, clusterer, label_matrix_simple, 0)

    labels_rsc = label_matrix_rsc.reshape(label_matrix_rsc.shape[1], )
    labels_rfs = label_matrix_rfs.reshape(label_matrix_rfs.shape[1], )
    labels_simple = label_matrix_simple.reshape(label_matrix_simple.shape[1], )

    nmis = []
    names = ["rfs", "rsc", "new"]
    label_arrs = [labels_rfs, labels_rsc, labels_simple]
    for i, entry in enumerate(label_arrs):
        print(f"{names[i]}: {np.unique(entry)} - nmi:", nmi(df_focus.label, entry))
        nmis.append(nmi(df_focus.label, entry))


    df_save = df_focus
    df_save["rsc"] = label_matrix_rsc.T
    df_save["rfs"] = label_matrix_rfs.T
    df_save["new"] = label_matrix_simple.T

    df_save.to_csv(output_path + f"Step{step}_gridpoint_{j}_results.csv")
    clean_labels= label_arrs[1]

    plot(clean_labels, df_focus, f"Run_{run}_gp_{j}_{names[1]}", output_path, icrs=True, return_fig=False)
    plot(label_arrs[0], df_focus, f"Run_{run}_gp_{j}_{names[0]}", output_path, icrs=True, return_fig=False)
    plot(label_arrs[2], df_focus, f"Run_{run}_gp_{j}_{names[2]}", output_path, icrs=True, return_fig=False)


    ##########
    # Output log-file
    all_fixed = {"step": step, "alpha": alpha, "beta": beta, "knn_initcluster_graph": knn_initcluster_graph,
                 "KNN": knn, "sfs_list": combo, "scaling": scaling, "bh_correction": bh,
                 names[np.argmax(nmis)]: np.max(nmis), "rsc": nmis[1]}

    filename = output_path + f"Parameters_gp_{j}.txt"
    with open(filename, 'w') as file:
        for key, value in all_fixed.items():
            file.write(f"{key} = {value}\n")
    ###########

    outer[j, :3] = nmis
    #outer_nmis.append(np.max(nmis))
    #outer_names.append(names[np.argmax(nmis)])
    outer[j, 3:] = [(len(np.unique(i))-1) for i in label_arrs]
    print(len(np.unique(clean_labels))-1)

#ummary_df = pd.DataFrame(data=np.column_stack([outer_names, outer_nmis, outer_n]), columns=["method", "nmi", "n_clusters"])
summary_df = pd.DataFrame(data=outer, columns=["nmi_rfs", "nmi_rsc", "nmi_new", "n_rfs", "n_rsc", "n_new"])
summary_df.to_csv(output_path+f"{run}_sn_{sn}_knn_{knn}_bh_{bh}_summary.csv")


--- Gridpoint 0 ---
Creating k-d trees of resampled data sets...
Performing clustering for scale factor [1.1433815784517884, 1.1323692287944023, 6.242815832643759]...
Performing gradient ascend using a 30-NN density estimation.
rfs: [-1.  0.  1.  2.  3.  4.] - nmi: 0.8202021734356035
rsc: [-1.  0.  1.  2.  3.  4.] - nmi: 0.8202021734356035
new: [-1.  0.  1.  2.  3.  4.] - nmi: 0.8192117864438372
5
--- Gridpoint 1 ---
Creating k-d trees of resampled data sets...
Performing clustering for scale factor [1.1433815784517884, 1.1323692287944023, 6.242815832643759]...
Performing gradient ascend using a 30-NN density estimation.
rfs: [-1.  0.  1.  2.  3.  4.] - nmi: 0.8211855447237417
rsc: [-1.  0.  1.  2.] - nmi: 0.7623711766906568
new: [-1.  0.  1.  2.  3.  4.] - nmi: 0.8210640655686009
3
--- Gridpoint 2 ---
Creating k-d trees of resampled data sets...
Performing clustering for scale factor [1.1433815784517884, 1.1323692287944023, 6.242815832643759]...
Performing gradient ascend using a 30-N